In [9]:
import sys
import MDAnalysis as mda
import prolif as plf
import prolif
from rdkit import Chem
from rdkit import Geometry
import py3Dmol
from prolif.plotting.network import LigNetwork
import numpy as np
from tqdm import tqdm
import os

'''
conda create -n prolif
conda activate prolif
conda config --add channels conda-forge
conda install rdkit cython
pip install git+https://github.com/chemosim-lab/ProLIF.git
pip install py3Dmol
'''

def TotalAtomNumber(top):
    tu = mda.Universe(top)
    atomnum=len(tu.atoms)
    return atomnum
    

def TrimTrajectoryFile(traj,guestlastindex):
    newtraj=traj.replace('.arc','_trim.arc')
    if not os.path.isfile(newtraj):
        temp=open(newtraj,'w')
        with open(traj) as infile:
            for line in infile:
                linesplit=line.split()
                if len(linesplit)==1:
                    temp.write(str(guestlastindex)+'\n')
                boxline=False
                if '90.000' in line and len(linesplit)==6:
                    boxline=True
                if boxline==False and len(linesplit)!=1:
                    index=int(linesplit[0])
                    if index<=guestlastindex:
                        temp.write(line)
    return newtraj


def get_ring_centroid(mol, index):
    # find ring using the atom index
    Chem.SanitizeMol(mol, Chem.SanitizeFlags.SANITIZE_SETAROMATICITY)
    ri = mol.GetRingInfo()
    for r in ri.AtomRings():
        if index in r:
            break
    else:
        raise ValueError("No ring containing this atom index was found in the given molecule")
    # get centroid
    coords = mol.xyz[list(r)]
    ctd = plf.utils.get_centroid(coords)
    return Geometry.Point3D(*ctd)


def GenerateHostGuestInteractionFingerprint(top,traj,firstframe,lastframe,framestep):
    u = mda.Universe(top,traj)
    prot = u.select_atoms("protein")
    lig = u.select_atoms("resname LIG")
    fp = prolif.Fingerprint(['Hydrophobic','HBDonor', 'HBAcceptor', 'PiStacking', 'Anionic', 'Cationic', 'CationPi', 'PiCation'])
    fp.run(u.trajectory[firstframe:lastframe:framestep], lig, prot)
    df = fp.to_dataframe(return_atoms=True)
    print(df)
    lmol = plf.Molecule.from_mda(lig)
    pmol = plf.Molecule.from_mda(prot)
    return lmol,pmol,df,u,prot,lig

def GenerateProLigInteraction3DView(df,lmol,pmol,prot,lig,u,firstframe,tol):
    
    colors = {
        "Hydrophobic": "red",
        "HBDonor": "orange",
        "HBAcceptor": "yellow",
        "PiStacking": "green",
        "Anionic": "blue",
        "Cationic": "indigo",
        "CationPi": "purple",
        "PiCation": "black",
    }

    for interaction,color in colors.items():
        print('Interaction:'+interaction+' Color:'+color)
    
    # JavaScript functions
    resid_hover = """function(atom,viewer) {{
        if(!atom.label) {{
            atom.label = viewer.addLabel('{0}:'+atom.atom+atom.serial,
                {{position: atom, backgroundColor: 'mintcream', fontColor:'black'}});
        }}
    }}"""
    hover_func = """
    function(atom,viewer) {
        if(!atom.label) {
            atom.label = viewer.addLabel(atom.interaction,
                {position: atom, backgroundColor: 'black', fontColor:'white'});
        }
    }"""
    unhover_func = """
    function(atom,viewer) {
        if(atom.label) {
            viewer.removeLabel(atom.label);
            delete atom.label;
        }
    }"""

    v = py3Dmol.view(650, 600)
    v.removeAllModels()

    models = {}
    mid = -1
    for i, row in df.T.iterrows():
        lresid, presid, interaction = i
        lindex, pindex = row[firstframe]
        lres = lmol[lresid]
        pres = pmol[presid]
        # set model ids for reusing later
        for resid, res, style in [(lresid, lres, {"colorscheme": "cyanCarbon"}),
                                  (presid, pres, {})]:
            if resid not in models.keys():
                mid += 1
                v.addModel(Chem.MolToMolBlock(res), "sdf")
                model = v.getModel()
                model.setStyle({}, {"stick": style})
                # add residue label
                model.setHoverable({}, True, resid_hover.format(resid), unhover_func)
                models[resid] = mid
        # get coordinates for both points of the interaction
        if interaction in ["PiStacking", "EdgeToFace", "FaceToFace", "PiCation"]:
            p1 = get_ring_centroid(lres, lindex)
        else:
            p1 = lres.GetConformer().GetAtomPosition(lindex)
        if interaction in ["PiStacking", "EdgeToFace", "FaceToFace", "CationPi"]:
            p2 = get_ring_centroid(pres, pindex)
        else:
            p2 = pres.GetConformer().GetAtomPosition(pindex)
        # add interaction line
        v.addCylinder({"start": dict(x=p1.x, y=p1.y, z=p1.z),
                       "end":   dict(x=p2.x, y=p2.y, z=p2.z),
                       "color": colors[interaction],
                       "radius": .15,
                       "dashed": True,
                       "fromCap": 1,
                       "toCap": 1,
                      })
        # add label when hovering the middle of the dashed line by adding a dummy atom
        c = Geometry.Point3D(*plf.utils.get_centroid([p1, p2]))
        modelID = models[lresid]
        model = v.getModel(modelID)
        model.addAtoms([{"elem": 'Z',
                         "x": c.x, "y": c.y, "z": c.z,
                         "interaction": interaction}])
        model.setStyle({"interaction": interaction}, {"clicksphere": {"radius": .5}})
        model.setHoverable(
            {"interaction": interaction}, True,
            hover_func, unhover_func)

    # show protein:
    # first we need to reorder atoms as in the original MDAnalysis file.
    # needed because the RDKitConverter reorders them when infering bond order
    # and 3Dmol.js doesn't like when atoms from the same residue are spread accross the whole file
    order = np.argsort([atom.GetIntProp("_MDAnalysis_index") for atom in pmol.GetAtoms()])
    mol = Chem.RenumberAtoms(pmol, order.astype(int).tolist())
    mol = Chem.RemoveAllHs(mol)
    pdb = Chem.MolToPDBBlock(mol, flavor=0x20 | 0x10)
    v.addModel(pdb, "pdb")
    model = v.getModel()
    model.setStyle({}, {"cartoon": {"style":"edged"}})
    coords=lig.positions
    resnames=GrabNearbyResidues(u,tol)
    for o in resnames:
        resname=o[0]
        resid=o[1]
        if resname!='LIG':
            v.addLabel(resname+str(resid),{'fontOpacity':1},{'resi':int(resid)})
        

     
    v.zoomTo({"model": list(models.values())})
    return v

def GrabNearbyResidues(u,tol):
    atoms=u.select_atoms("around "+str(tol)+' '+'resname '+'LIG')
    resnames=[]
    for atom in atoms:
        resname=atom.resname
        resid=atom.resid
        tup=[resname,resid]
        if tup not in resnames:
            resnames.append(tup)
    return resnames

def MD_visualization(top, traj_end,stride_animation,tol):
  """
  Inputs: 
  top : path to the topology file
  traj_end : path to the trajectory file
  """
  # Instance of the Universe class
  u = mda.Universe(top, traj_end)

  # The number of frames in the simulation
  number_frames_analysis = len(u.trajectory)

  # Deleting previously stored frames as PDBs and removing warnings
  import warnings
  warnings.filterwarnings('ignore')
  !rm [0-9]?.pdb 2> /dev/null
  
    # Helper classes to read and get PDB fields
  class Atom(dict):
    def __init__(self, line):
      self["type"] = line[0:6].strip()
      self["idx"] = line[6:11].strip()
      self["name"] = line[12:16].strip()
      self["resname"] = line[17:20].strip()
      self["resid"] = int(int(line[22:26]))
      self["x"] = float(line[30:38])
      self["y"] = float(line[38:46])
      self["z"] = float(line[46:54])
      self["sym"] = line[76:78].strip()

    def __str__(self):
      line = list(" " * 80)
      line[0:6] = self["type"].ljust(6)
      line[6:11] = self["idx"].ljust(5)
      line[12:16] = self["name"].ljust(4)
      line[17:20] = self["resname"].ljust(3)
      line[22:26] = str(self["resid"]).ljust(4)
      line[30:38] = str(self["x"]).rjust(8)
      line[38:46] = str(self["y"]).rjust(8)
      line[46:54] = str(self["z"]).rjust(8)
      line[76:78] = self["sym"].rjust(2)
      return "".join(line) + "\n"
          
  class Molecule(list):
    def __init__(self, file):
      for line in file:
        if "ATOM" in line or "HETATM" in line:
          self.append(Atom(line))
              
      def __str__(self):
        outstr = ""
        for at in self:
          outstr += str(at)
        return outstr
  # Write out frames for animation
  # IMPORTANT: This line will filter the WATER molecules.
  protein = u.select_atoms('not (resname WAT)') 
  i = 0
  for ts in tqdm(u.trajectory[0:len(u.trajectory):int(stride_animation)],desc='Read ARC, Write PDB'): 
      if i > -1:
          with mda.Writer('' + str(i) + '.pdb', protein.n_atoms) as W:
              W.write(protein)
      i = i + 1
  # Load frames as molecules (py3Dmol let us visualize a single "molecule" per frame)
  molecules = []
  for i in tqdm(range(int(len(u.trajectory)/int(stride_animation))),desc='Reading PDBs, make Molecule'):
      with open('' + str(i) + '.pdb') as ifile:
          molecules.append(Molecule(ifile))

  models = ""
  for i in tqdm(range(len(molecules)),desc='Creating MODEL string for animation'):
    models += "MODEL " + str(i) + "\n"
    for j,mol in enumerate(molecules[i]):
      models += str(mol)
    models += "ENDMDL\n"
  for atom in lig:
      ligresid=atom.resid
      break
    
  resnames=GrabNearbyResidues(u,tol)

  # Animation
  view = py3Dmol.view(width=800, height=600)
  view.addModelsAsFrames(models)
  view.setStyle({}, {"cartoon": {'color': 'spectrum'}})
  view.addStyle({'resi':int(ligresid)},{'sphere':{'colorscheme':'greenCarbon'}})
  for o in resnames:
      resname=o[0]
      resid=o[1]
      view.addStyle({'resi':int(resid)},{'stick':{'colorscheme':'greenCarbon'}})
 
          

  view.zoomTo()
  view.animate({'loop': "forward"})
  return view

In [2]:
traj='C:/Users/brand/OneDrive/Desktop/melk_CompE1_V1_R0_compboxproddyn.arc'
top='C:/Users/brand/OneDrive/Desktop/topologyguess.pdb'
framestep=100
firstframe=50
lastframe=51
guestlastindex=TotalAtomNumber(top)
newtraj=TrimTrajectoryFile(traj,guestlastindex)
lmol,pmol,df,u,prot,lig=GenerateHostGuestInteractionFingerprint(top,newtraj,firstframe,lastframe,framestep)

100%|████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:20<00:00, 20.82s/it]


ligand             LIG2                                                  \
protein         CYS71.B    GLU118.B     GLU75.B      GLY2.B     GLY74.B   
interaction Hydrophobic Hydrophobic Hydrophobic Hydrophobic Hydrophobic   
Frame                                                                     
50               (7, 6)     (34, 2)     (34, 6)      (9, 1)     (13, 1)   

ligand                                                                   
protein        ILE131.B    LEU121.B     PRO72.B     TYR70.B      VAL7.B  
interaction Hydrophobic Hydrophobic Hydrophobic Hydrophobic Hydrophobic  
Frame                                                                    
50              (32, 9)      (4, 9)     (18, 2)      (7, 8)      (7, 7)  


In [19]:
net = LigNetwork.from_ifp(df, lmol,
                              # replace with `kind="frame", frame=0` for the other depiction
                              kind="aggregate", threshold=.3,
                              rotation=270)
net.display()


C:\Users\brand\miniconda3\envs\prolif\lib\site-packages\pandas\core\algorithms.py:798: FutureWarning: In a future version, the Index constructor will not infer numeric dtypes when passed object-dtype sequences (matching Series behavior)
  uniques = Index(uniques)


In [10]:
stride_animation=500
tol=4 # how many angstroms away from ligand com to show AA labels
view = MD_visualization(top, newtraj,stride_animation,tol)
view.show()


The system cannot find the path specified.
Creating MODEL string for animation: 100%|███████████████████████████████████████████████| 5/5 [00:01<00:00,  4.50it/s]


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [43]:
v = GenerateProLigInteraction3DView(df,lmol,pmol,prot,lig,u,firstframe,tol)
v.show()

Interaction:Hydrophobic Color:red
Interaction:HBDonor Color:orange
Interaction:HBAcceptor Color:yellow
Interaction:PiStacking Color:green
Interaction:Anionic Color:blue
Interaction:Cationic Color:indigo
Interaction:CationPi Color:purple
Interaction:PiCation Color:black


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol